In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from pathlib import Path

try:
    from google.colab import drive

    drive.mount("/content/drive")
    workding_dir = "/content/drive/MyDrive/logical-reasoning/"
except ModuleNotFoundError:
    workding_dir = str(Path.cwd().parent)

In [3]:
import os
import sys
from pathlib import Path

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/logical-reasoning


In [4]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /home/inflaton/code/projects/courses/logical-reasoning/.env


True

In [5]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"


print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full None False datasets/mgtv results/mgtv-results_merged_model.csv


In [6]:
%%time
!python --version
!pip show flash-attn
!pip show transformers

Python 3.11.9
Name: transformers
Version: 4.43.0.dev0
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /home/inflaton/miniconda3/envs/llama-factory/lib/python3.11/site-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenizers, tqdm
Required-by: llamafactory, peft, trl, vllm
CPU times: user 13.4 ms, sys: 20.3 ms, total: 33.6 ms
Wall time: 1.8 s


In [7]:
from llm_toolkit.llm_utils import *
from llm_toolkit.logical_reasoning_utils import *

device = check_gpu()

loading /home/inflaton/code/projects/courses/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
GPU is available


In [8]:
%%time

model, tokenizer = load_model(model_name)

loading model: llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

CPU times: user 1min 43s, sys: 917 ms, total: 1min 44s
Wall time: 1min 58s


In [9]:
datasets = load_logical_reasoning_dataset(
    data_path,
    tokenizer=tokenizer,
    chinese_prompt=not use_english_datasets,
    using_p1=False,
)

loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 25000
    })
    test: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 3000
    })
})


In [10]:
%%time

prompt1 = datasets["test"]["prompt"][1000]
print(prompt1)
print("--" * 20)
test_model(model, tokenizer, prompt1, device=device)

<s><|im_start|>system
You are an expert in logical reasoning.<|im_end|>
<|im_start|>user
你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一个简单又难以理解的事件。
2. 主持人知道谜底，谜底是谜面的答案。
3. 参与者可以询问任何封闭式问题来找寻事件的真相。
4. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。各回答的判断标准如下：
   - 若谜面和谜底能找到问题的答案，回答：是或者不是
   - 若谜面和谜底不能直接或者间接推断出问题的答案，回答：不重要
   - 若参与者提问不是一个封闭式问题或者问题难以理解，回答：问法错误
   - 若参与者提问基本还原了谜底真相，回答：回答正确
5. 回答中不能添加任何其它信息，也不能省略选项中的任何一个字。例如，不可以把“不是”省略成“不”。

请严格按照这些规则回答参与者提出的问题。

**谜面:** 在一个安静的夜晚，小村庄的湖边突然传来了阵阵哭泣声。第二天早晨，村长甄锐发现湖边的石头上放着一顶破旧的帽子，但没有人知道这顶帽子是从哪里来的，哭泣声又是为何。请还原故事真相。

**谜底:** 原来，这顶破旧的帽子属于一个小男孩，他小时候与爷爷在湖边生活。爷爷教他钓鱼、游泳，还告诉他湖中的海龟是他们的朋友。后来，小男孩随父母去了城市生活，但每年夏天都会回到村子探望爷爷。然而，去年夏天，爷爷因病去世，小男孩伤心欲绝。今年夏天，他回到村子，来到湖边，想起和爷爷的美好回忆，忍不住哭泣。他将爷爷的帽子放在湖边的石头上，希望能让爷爷的在天之灵得到安慰。那晚的哭泣声正是小男孩在祭莫他亲爱的爷爷。

**参与者提出的问题:** 哭泣和村庄有关系吗
<|im_end|>
<|im_start|>assistant

----------------------------------------
<s><s><|im_start|>system
You are an expert in logical reasoning.<|im_end|>
<|im_start|>user
你是一个情景猜谜游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜面，谜面会描述一

In [11]:
%%time

eval_model(model, tokenizer, datasets["test"][:10], device=device, repetition_penalty=1.0)

 12%|█▎        | 1/8 [00:01<00:11,  1.62s/it]

--------
step 1: 不是</s>
--------
step 2: 不是
--------
step 3: 不是
--------
step 4: 不是
--------
step 5: 不是


100%|██████████| 8/8 [00:12<00:00,  1.52s/it]

CPU times: user 11.3 s, sys: 386 ms, total: 11.7 s
Wall time: 12.2 s


['不是', '是', '是', '是', '不是', '是', '不重要', '不是']

In [14]:
def evaluate_model(model, tokenizer, model_name, dataset):
    print(f"Evaluating model: {model_name} on {device}")
    predictions = eval_model(
        model, tokenizer, dataset, device=device, repetition_penalty=1.0
    )

    model_name += "_NV4080_rp1.0"

    save_results(
        model_name,
        results_path,
        dataset,
        predictions,
        debug=True,
    )

    metrics = calc_metrics(dataset["label"], predictions, debug=True)
    print(metrics)

In [18]:
repetition_penalty = 1.01
f"{repetition_penalty: .2f}"

' 1.01'

In [15]:
%%time

evaluate_model(model, tokenizer, model_name, datasets["test"])

Evaluating model: llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full on cuda


  0%|          | 1/3000 [00:01<1:23:59,  1.68s/it]

--------
step 1: 不是</s>
--------
step 2: 不是
--------
step 3: 不是
--------
step 4: 不是
--------
step 5: 不是


100%|██████████| 3000/3000 [1:47:43<00:00,  2.15s/it]  


      text label title                                             puzzle  \
0  甄加索是自杀吗    不是  海岸之谜  在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任...   

                                               truth  \
0  甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在...   

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_epoch_6_NV4080  \
0                                                 不是                                   

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_epoch_6_M3  \
0                                                 不是                               

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_NV4080  \
0                                                 不是                           

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_M3  \
0                                                 不是                       

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_NV

In [19]:
import numpy as np


def evaluate_model_with_repetition_penalty(
    model,
    tokenizer,
    model_name,
    dataset,
    start_repetition_penalty=1.01,
    end_repetition_penalty=1.09,
    step_repetition_penalty=0.01,
):
    print(f"Evaluating model: {model_name} on {device}")

    for repetition_penalty in np.arange(
        start_repetition_penalty,
        end_repetition_penalty + step_repetition_penalty,
        step_repetition_penalty,
    ):
        print(f"*** Evaluating with repetition_penalty: {repetition_penalty}")
        predictions = eval_model(
            model,
            tokenizer,
            dataset,
            device=device,
            repetition_penalty=repetition_penalty,
        )

        model_name_with_rp = f"{model_name}_NV4080_rp{repetition_penalty}"

        save_results(
            model_name_with_rp,
            results_path,
            dataset,
            predictions,
            debug=True,
        )

        metrics = calc_metrics(dataset["label"], predictions, debug=True)
        print(metrics)

In [20]:
evaluate_model_with_repetition_penalty(model, tokenizer, model_name, datasets["test"])

Evaluating model: llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full on cuda
*** Evaluating with repetition_penalty: 1.01


  0%|          | 1/3000 [00:01<1:33:41,  1.87s/it]

--------
step 1: 不是</s>
--------
step 2: 不是
--------
step 3: 不是
--------
step 4: 不是
--------
step 5: 不是


100%|██████████| 3000/3000 [1:51:19<00:00,  2.23s/it]  


      text label title                                             puzzle  \
0  甄加索是自杀吗    不是  海岸之谜  在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任...   

                                               truth  \
0  甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在...   

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_epoch_6_NV4080  \
0                                                 不是                                   

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_epoch_6_M3  \
0                                                 不是                               

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_NV4080  \
0                                                 不是                           

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_M3  \
0                                                 不是                       

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_NV

...

      text label title                                             puzzle  \
0  甄加索是自杀吗    不是  海岸之谜  在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任...   

                                               truth  \
0  甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在...   

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_epoch_6_NV4080  \
0                                                 不是                                   

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_epoch_6_M3  \
0                                                 不是                               

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_NV4080  \
0                                                 不是                           

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_M3  \
0                                                 不是                       

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_NV

  0%|          | 1/3000 [00:02<2:06:54,  2.54s/it]

--------
step 1: 不是</s>
--------
step 2: 不是
--------
step 3: 不是
--------
step 4: 不是
--------
step 5: 不是


100%|██████████| 3000/3000 [1:57:59<00:00,  2.36s/it]  


      text label title                                             puzzle  \
0  甄加索是自杀吗    不是  海岸之谜  在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任...   

                                               truth  \
0  甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在...   

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_epoch_6_NV4080  \
0                                                 不是                                   

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_epoch_6_M3  \
0                                                 不是                               

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_NV4080  \
0                                                 不是                           

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_M3  \
0                                                 不是                       

  llama-factory/merged_models/internlm2_5-7b-chat-1m_sft_bf16_p2_full_NV